In [1]:
import scrapy
import numpy as np
from scrapy.crawler import CrawlerProcess
import re
import json

In [2]:
class Diputados(scrapy.Spider):
    name = "spider_diputados"
    
    def start_requests(self):
        links = [urlCurr + i for i in terminaciones]
        for link in links:
            yield scrapy.Request( url = link, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'}, 
                              callback = self.parse )
    
    def parse(self,response):
        nombre = response.css('td.textocurrienc > center > strong::text').get()
        nombre = limpiaNom(nombre) # cambié esto
        idDipu = ''.join([c for c in nombre[1:] if c.isupper()])
        cumple = response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[6]
        curp = creaCurp(nombre,cumple)
        dipus[curp]={}
        dipus.get(curp,{})['CURP']=curp # Agregué esto para 
        dipus.get(curp,{})['Nombre']=nombre # cambié aquí
        dipus.get(curp,{})['TipoElección']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract_first()
        dipus.get(curp,{})['Entidad']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[1]
        parti=response.xpath('//table[@class="cajasombra"]//img/@src').extract()[1]
        dipus.get(curp,{})['Partido']=obtienePartido(parti)
        distri1 =response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[2]
        distri2 =response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[3]  # PARTE RARA
        dipus.get(curp,{})['Distrito'] = distri1 +""+ distri2
        dipus.get(curp,{})['Correo']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[4]
        dipus.get(curp,{})['Extensión']=response.css('td.textocurri:nth-of-type(2) > strong::text').extract()[5]
        dipus.get(curp,{})['Onomástico']=cumple
        supl=response.css('td.textocurri:nth-of-type(2)::text').extract()[6]
        dipus.get(curp,{})['Suplente']=limpiaText(supl)
        dipus.get(curp,{})['Comisiones']=response.xpath('//a[contains(@href, "integrantes_de_comision")]/text()').getall()
        dipus.get(curp,{})['Último grado de estudios']=response.xpath('//td[@class="textoNegro"]/text()').extract_first()
        link_asis=urlDipu + response.css('table.tableInfo  a::attr(href)').extract()[0]
        link_votaciones=urlDipu + response.css('table.tableInfo  a::attr(href)').extract()[1]
        yield response.follow(url=link_asis, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse2)
        yield response.follow(url=link_votaciones, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse4)
    
    def parse2(self,response):
        curp = response.meta['curp']
        referencias = response.xpath('//a[@class="linkVerde"]/@href').extract()
        links = [urlDipu + referencia for referencia in referencias]
        for li in links:
            yield response.follow(url=li, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse3)
    
    def parse3(self,response):
        curp = response.meta['curp']
        prueba = response.xpath('//tr/td/div/font/text()').extract()
        dias = list(filter(lambda a: (a == 'A' or a =='AC'), prueba))
        dipus.get(curp,{})['Asistencias']=dipus.get(curp,{}).get('Asistencias',0) + len(dias)

    def parse4(self,response):
        curp = response.meta['curp']
        referencias = response.xpath('//a[@class="linkVerde"]/@href').extract()
        links = [urlDipu + referencia for referencia in referencias]
        for li in links:
            yield response.follow(url=li, headers={'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:66.0) Gecko/20100101 Firefox/66.0'},meta={'curp':curp},
                              callback=self.parse5)
                
    def parse5(self,response):
        curp = response.meta['curp']
        aux = response.xpath('//td[@class="smallVerde"]/text()').extract()
        aux2={}
        for i in range(1,len(aux),4):
            votos = {}
            votacion = response.xpath('//td[@class="smallVerde"]/text()').extract()[i]
            posi = response.xpath('//td[@class="smallVerde"]/text()').extract()[i+2]
            if(votacion in por_votaciones.keys()):
                por_votaciones[votacion][curp]=posi
            else:
                por_votaciones[votacion] = {curp:posi}
            votos['votación']=votacion
            votos['posición']=posi
            aux2['votos']=aux2.get('votos', []) + [votos]
            #dipus.get(curp,{})['votos']=dipus.get(curp,{}).get('votos', []) + [votos]
        dipus.get(curp,{})['votos']=dipus.get(curp,{}).get('votos',0)+len(aux2.get('votos', [])) # Se comenta si la de arriba se descomenta


        

In [3]:
def creaCurp(nombre,cumple):
    
    '''
    iniciales = ''.join([c for c in nombre[1:] if c.isupper()])
    c = cumple.replace('-', ' ').split(' ')
    if(len(c[0])==1):
        c[0]="0"+c[0] 
    curp = iniciales[0:3]+c[0]+c[1][0:3]+c[2][-2:]
    '''
    curp = nombre.replace(' ', '')
    curp = curp.upper()
    curp = curp.replace('Á', 'A')
    curp = curp.replace('É', 'E')
    curp = curp.replace('Í', 'I')
    curp = curp.replace('Ó', 'O')
    curp = curp.replace('Ú', 'U')
    curp = curp.replace('Ñ', 'N')
    return curp

In [4]:
def limpiaText(nom):
    resp = re.sub('\s+',' ',nom)
    resp = resp[0:len(resp)-1]
    return resp

In [5]:
def limpiaNom(nom):
    resp = nom.replace('Dip. ', '')
    resp = resp.replace(' (LICENCIA)', '')
    return resp

In [6]:
def obtienePartido(imagen):
    res=""
    if(imagen=='images/pan.png'):
        res = "PAN"
    elif(imagen=='images/Logo_PT.png'):
        res = "PT"
    elif(imagen=='images/LogoMorena.jpg'):
        res = "Morena"
    elif(imagen=='images/encuentro.png'):
        res = "Encuentro Social"
    elif(imagen=='images/logo_movimiento_ciudadano.png'):
        res = "Movimiento Ciudadano"
    elif(imagen=='images/pri01.png'):
        res = "PRI"
    elif(imagen=='images/logvrd.jpg'):
        res = "Partido Verde"
    elif(imagen=='images/prd01.png'):
        res = "PRD"
    elif(imagen=='images/logo_SP.jpg'):
         res = "Sin Partido"
    else:
         res = imagen
    return res
                                    

In [7]:
dipus={}
curp = "h"
urlDipu = "http://sitl.diputados.gob.mx/LXIV_leg/"
urlCurr = "http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt="

por_votaciones = {}

terminaciones = []
for i in range(0,5):
    for j in range(0,10):
        for k in range(0,10):
            terminaciones.append(str(i)+str(j)+str(k))
terminaciones.append(str(500))
terminaciones.pop(0)


# Run the Spider
process = CrawlerProcess()
process.crawl(Diputados)
process.start()


2021-04-08 18:58:47 [scrapy.utils.log] INFO: Scrapy 2.4.1 started (bot: scrapybot)
2021-04-08 18:58:47 [scrapy.utils.log] INFO: Versions: lxml 4.6.2.0, libxml2 2.9.5, cssselect 1.1.0, parsel 1.6.0, w3lib 1.22.0, Twisted 21.2.0, Python 3.8.2 (tags/v3.8.2:7b3ab59, Feb 25 2020, 23:03:10) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 20.0.1 (OpenSSL 1.1.1j  16 Feb 2021), cryptography 3.4.6, Platform Windows-10-10.0.19041-SP0
2021-04-08 18:58:47 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2021-04-08 18:58:47 [scrapy.crawler] INFO: Overridden settings:
{}
2021-04-08 18:58:47 [scrapy.extensions.telnet] INFO: Telnet Password: bc387604d8f26b70
2021-04-08 18:58:47 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.logstats.LogStats']
2021-04-08 18:58:48 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddl

2021-04-08 18:58:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=015> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=015)
2021-04-08 18:58:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=017> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=017)
2021-04-08 18:58:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=003> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=003)
2021-04-08 18:58:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=014> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=014)
2021-04-08 18:58:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.g

2021-04-08 18:59:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=13> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-08 18:59:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=19&pert=15> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=019)
2021-04-08 18:59:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=19&pert=14> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=019)
2021-04-08 18:59:01 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=19&pert=15> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?di

2021-04-08 18:59:04 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=19&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=019)
2021-04-08 18:59:04 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=19&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=019)
2021-04-08 18:59:04 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=19&pert=9> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=019)
2021-04-08 18:59:04 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=19&pert=4> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=019)


2021-04-08 18:59:12 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=9> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-08 18:59:12 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-08 18:59:12 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=16> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)
2021-04-08 18:59:12 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=16&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=016)

...

2021-04-08 19:51:28 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=482> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=482)
2021-04-08 19:51:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=483> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=483)
2021-04-08 19:51:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=486> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=486)
2021-04-08 19:51:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=488> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=488)
2021-04-08 19:51:29 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.g

2021-04-08 19:51:33 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=486&pert=11> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=486)
2021-04-08 19:51:33 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=500> (referer: http://sitl.diputados.gob.mx/LXIV_leg/curricula.php?dipt=500)
2021-04-08 19:51:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=486&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=486)
2021-04-08 19:51:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=486&pert=6> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=486)
2021-04-08 19

2021-04-08 19:51:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=499&pert=15> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=499)
2021-04-08 19:51:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=499&pert=13> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=499)
2021-04-08 19:51:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=499&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=499)
2021-04-08 19:51:47 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=499&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt

2021-04-08 19:51:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=500&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=500)
2021-04-08 19:51:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=13> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=498)
2021-04-08 19:51:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=8> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.php?dipt=498)
2021-04-08 19:51:50 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/asistencias_por_pernplxiv.php?iddipt=498&pert=11> (referer: http://sitl.diputados.gob.mx/LXIV_leg/asistencias_diputados_xperiodonplxiv.

2021-04-08 19:51:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=482&pert=7> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=482)
2021-04-08 19:51:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=482&pert=6> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=482)
2021-04-08 19:51:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=482&pert=3> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=482)
2021-04-08 19:51:53 [scrapy.core.engine] DEBUG: Crawled (200) <GET http://sitl.diputados.gob.mx/LXIV_leg/votaciones_por_pernplxiv.php?iddipt=482&pert=11> (referer: http://sitl.diputados.gob.mx/LXIV_leg/votaciones_diputados_xperiodonplxiv.php?dipt=

In [8]:
list_of_dics = [value for value in dipus.values()]


[{'CURP': 'JESUSSALVADORMINORMORA',
  'Nombre': 'Jesús Salvador Minor Mora',
  'TipoElección': 'Mayoría Relativa',
  'Entidad': 'Baja California ',
  'Partido': 'Morena',
  'Distrito': '1 L-453 ',
  'Correo': 'jesus.minor@diputados.gob.mx ',
  'Extensión': '61368 ',
  'Onomástico': '1-junio-1951 ',
  'Suplente': 'Juan Melendrez Espinoza',
  'Comisiones': [' Asuntos Frontera Norte  ',
   ' Desarrollo y Conservación Rural, Agrícola y Autosuficiencia Alimentaria   ',
   ' Recursos Hidráulicos, Agua Potable y Saneamiento (Secretaría) '],
  'Último grado de estudios': 'Licenciatura',
  'Asistencias': 122,
  'votos': 627},
 {'CURP': 'MARIOISMAELMORENOGIL',
  'Nombre': 'Mario Ismael Moreno Gil',
  'TipoElección': 'Mayoría Relativa',
  'Entidad': 'Baja California ',
  'Partido': 'Morena',
  'Distrito': '5 L-452 ',
  'Correo': 'ismael.moreno@diputados.gob.mx ',
  'Extensión': '61327 ',
  'Onomástico': '17-junio-1948 ',
  'Suplente': 'Luis Javier Algorri Franco',
  'Comisiones': [' Cultura y Cin

In [8]:
for key, value in dipus.items():
    print('\n',key, ' : \n\n', value)


 JESUSSALVADORMINORMORA  : 

 {'CURP': 'JESUSSALVADORMINORMORA', 'Nombre': 'Jesús Salvador Minor Mora', 'TipoElección': 'Mayoría Relativa', 'Entidad': 'Baja California ', 'Partido': 'Morena', 'Distrito': '1 L-453 ', 'Correo': 'jesus.minor@diputados.gob.mx ', 'Extensión': '61368 ', 'Onomástico': '1-junio-1951 ', 'Suplente': 'Juan Melendrez Espinoza', 'Comisiones': [' Asuntos Frontera Norte  ', ' Desarrollo y Conservación Rural, Agrícola y Autosuficiencia Alimentaria   ', ' Recursos Hidráulicos, Agua Potable y Saneamiento (Secretaría) '], 'Último grado de estudios': 'Licenciatura', 'Asistencias': 122, 'votos': 627}

 ELBALORENATORRESDIAZ  : 

 {'CURP': 'ELBALORENATORRESDIAZ', 'Nombre': 'Elba Lorena Torres Díaz', 'TipoElección': 'Mayoría Relativa', 'Entidad': 'Aguascalientes ', 'Partido': 'PT', 'Distrito': '2 H-278 ', 'Correo': 'elba.torres@diputados.gob.mx ', 'Extensión': '62100 ', 'Onomástico': '15-marzo-1977 ', 'Suplente': 'Haydeé Hernández Muñoz', 'Comisiones': [' Salud (Secretaría) 

In [10]:
for key, value in por_votaciones.items():
    print('\n',key,': ')
    for curp, posi in value.items():
        print('\n',curp, ': ', posi)


 MINUTA CON PROYECTO DE DECRETO POR EL QUE SE EXPIDE LA LEY FEDERAL DE PROTECCIÓN A LA PROPIEDAD INDUSTRIAL (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 MINUTA CON PROYECTO DE DECRETO POR EL QUE SE EXPIDE LA LEY DE INFRAESTRUCTURA DE LA CALIDAD Y SE ABROGA LA LEY FEDERAL SOBRE METROLOGÍA Y NORMALIZACIÓN (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 MINUTA CON PROYECTO DE DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DEL CÓDIGO PENAL FEDERAL. (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 MINUTA CON PROYECTO DE DECRETO POR EL QUE SE REF

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN LOS ARTÍCULOS 58 DEL CÓDIGO CIVIL FEDERAL Y 19 DE LA LEY GENERAL DE LOS DERECHOS DE NIÑAS, NIÑOS Y ADOLESCENTES (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  En contra

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Abstención

 DECRETO POR EL QUE SE ADICIONA UNA FRACCIÓN XXX BIS AL ARTÍCULO 70 DE LA LEY GENERAL DE TRANSPARENCIA Y ACCESO A LA INFORMACIÓN PÚBLICA (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE ADICIONA UN TERCER PÁRRAFO AL ARTÍCULO 40 DE LA LEY DE CIENCIA Y TECNOLOGÍA (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE ADICION

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DE LA LEY ORGÁNICA DE LA ADMINISTRACIÓN PÚBLICA FEDERAL Y DE LA LEY GENERAL PARA LA PREVENCIÓN Y GESTIÓN INTEGRAL DE LOS RESIDUOS (EN LO GENERAL Y EN LO PARTICULAR, LOS ARTÍCULOS NO RESERVADOS)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DE LA LEY ORGÁNICA DE LA ADMINISTRACIÓN PÚBLICA FEDERAL Y DE LA LEY GENERAL PARA LA PREVENCIÓN Y GESTIÓN INTEGRAL DE LOS RESIDUOS (EN LO PARTICULAR LOS ARTICULOS RESERVADOS CON LAS MODIFICACIONES ACEPTADAS POR LA ASAMBLEA)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DIS

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE ADICIONA UNA FRACCIÓN XXXIV AL ARTÍCULO 9 DE LA LEY FEDERAL PARA PREVENIR Y ELIMINAR LA DISCRIMINACIÓN (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE ADICIONA UN ARTICULO 254 QUÁTER AL CÓDIGO PENAL FEDERAL (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE ADICIONA UN ARTÍCULO 258 BIS AL CÓDIGO NACIONAL DE PROCEDIMIENTOS PENALES (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN 

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE DECLARA LA ÚLTIMA SEMANA DE FEBRERO DE CADA AÑO COMO LA "SEMANA NACIONAL DE LA SALUD AUDITIVA" (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DE LA LEY GENERAL EN MATERIA DE DELITOS ELECTORALES (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  Ausente

 DECRETO POR EL QUE SE REFORMA EL ARTÍCULO 418 DEL CÓDIGO PENAL FEDERAL (EN LO GENERAL Y EN LO PARTICULAR)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  Ausente

 FRANCISCOJAVIERLUEVANONUNEZ :  Ausente

 MARTHAELISAGONZALEZESTRADA :  Ausente

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DE LA LEY F

 FRANCISCOJAVIERLUEVANONUNEZ :  En contra

 DECRETO POR EL QUE SE EXPIDE LA LEY FEDERAL PARA LA REGULACIÓN DEL CANNABIS, Y SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DE LA LEY GENERAL DE SALUD Y DEL CÓDIGO PENAL FEDERAL (EN LO PARTICULAR LOS ARTÍCULOS RESERVADOS EN TÉRMINOS DEL DICTAMENS Y CON LAS MODIFICACIONES ACEPTADAS POR LA ASAMBLEA)  : 

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  En contra

 DECRETO POR EL QUE SE REFORMAN Y ADICIONAN DIVERSAS DISPOSICIONES DE LA LEY GENERAL DE CULTURA FÍSICA Y DEPORTE (EN LO GENERAL Y EN LO PARTICULAR)  : 

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 DECRETO POR EL QUE SE REFORMA LA FRACCIÓN XII DEL ARTÍCULO 2 DE LA LEY GENERAL DE CULTURA FÍSICA Y DEPORTE (EN LO GENERAL Y EN LO PARTICULAR)  : 

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 DECRETO POR EL QUE SE REFORMA Y ADICIONA EL ARTÍCULO 112 DE LA LEY GENERAL DE LOS DERECHOS DE NIÑAS, NIÑOS Y ADOLES

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE REFORMAN, ADICIONAN Y DEROGAN DIVERSAS DISPOSICIONES DE LAS LEYES FEDERAL DEL TRABAJO, ORGÁNICA DEL PODER JUDICIAL DE LA FEDERACIÓN, FEDERAL DE LA DEFENSORÍA PÚBLICA, DEL INSTITUTO DEL FONDO NACIONAL DE LA VIVIENDA PARA LOS TRABAJADORES, Y DEL SEGURO SOCIAL, EN MATERIA DE JUSTICIA LABORAL, LIBERTAD SINDICAL Y NEGOCIACIÓN COLECTIVA (EN LO GENERAL Y EN LO PARTICULAR LOS ARTÍCULOS NO RESERVADOS)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  A favor

 MARTHAELISAGONZALEZESTRADA :  A favor

 DECRETO POR EL QUE SE REFORMAN, ADICIONAN Y DEROGAN DIVERSAS DISPOSICIONES DE LAS LEYES FEDERAL DEL TRABAJO, ORGÁNICA DEL PODER JUDICIAL DE LA FEDERACIÓN, FEDERAL DE LA DEFENSORÍA PÚBLICA, DEL INSTITUTO DEL FONDO NACIONAL DE LA VIVIENDA PARA LOS TRABAJADORES, Y DEL SEGURO 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  En contra

 MARTHAELISAGONZALEZESTRADA :  En contra

 DECRETO DE PRESUPUESTO DE EGRESOS DE LA FEDERACIÓN PARA EL EJERCICIO FISCAL DE 2019 (EN LO PARTICULAR LOS ARTÍCULOS O ANEXOS RESERVADOS, EN TÉRMINOS DEL DICTAMEN O CON LAS MODIFICACIONES ACEPTADAS POR LA ASAMBLEA)  : 

 ELBALORENATORRESDIAZ :  A favor

 JESUSSALVADORMINORMORA :  A favor

 FRANCISCOJAVIERLUEVANONUNEZ :  Ausente

 MARTHAELISAGONZALEZESTRADA :  Ausente


In [9]:
with open('diputados.json', 'a') as f:
            json.dump(list_of_dics, f, indent=4, ensure_ascii=False) # antes dipus

In [10]:
with open('votaciones.json', 'a') as f:
            json.dump(por_votaciones, f, indent=4, ensure_ascii=False)

In [18]:
limpiaText("Ma. Guadalupe Loredo Gonzáles\n\t\t\t\t\t\n\n\n ")

'Ma. Guadalupe Loredo Gonzáles'

In [9]:
"Dip. Martha Elisa González Estrada (LICENCIA)".replace(' (LICENCIA)', '')

'Dip. Martha Elisa González Estrada'